In [71]:
!pip install nglview --user

/usr/lib/python3/dist-packages/secretstorage/dhcrypto.py:15: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
/usr/lib/python3/dist-packages/secretstorage/util.py:19: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
You should consider upgrading via the '/usr/bin/python3 -m pip install --upgrade pip' command.


Импортирую необходимое

In [72]:
import nglview as nv
import requests
import json



<h1> Задание №1 </h1>

Формирую заготовку запроса:

In [73]:
my_query = {
    "query": {
        "type": "group",
        "logical_operator": "and",
        "nodes": []
    },
    "return_type": "entry"
}

Записываю все условия

Формирую запрос на ключевое слово <i>"prednisolone"</i>:

In [74]:
keyword_clause= {"type": "terminal",
                "service": "full_text",
                "parameters": {"value": "prednisolone"}}
my_query["query"]["nodes"].append(keyword_clause)

Формирую запрос на разрешение не хуже 2.6:

In [75]:
resolution_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "value": 2.6,
        "attribute": "rcsb_entry_info.resolution_combined",
        "operator": "less_or_equal"
    }
}

my_query["query"]["nodes"].append(resolution_clause)

Формирую запрос на число лигандов не меньше 1:

In [76]:
has_ligand_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "attribute": "rcsb_entry_info.nonpolymer_entity_count",
        "value": 0,
        "operator": "greater"
    }
}

my_query["query"]["nodes"].append(has_ligand_clause)

Формирую запрос на предоставление нужной даты появления структуры:

In [77]:
date_range_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "attribute": "rcsb_accession_info.initial_release_date",
        "value": {
            "from": "2020-01-01",
            "to": "2023-01-01",
        },
        "operator": "range"
    }
}

my_query["query"]["nodes"].append(date_range_clause)

Направляю запрос на сайт:

In [78]:
rcsb = 'https://search.rcsb.org/rcsbsearch/v1/query'

json_query = json.dumps(my_query)
search = requests.post(f'{rcsb}', data=json_query)

In [79]:
search

<Response [200]>

Получаю и анализирую результаты поиска:

In [80]:
search_result = search.json() 
search_result

{'query_id': '44fea03f-f549-4266-b4f6-471f2ee3c5fa',
 'result_type': 'entry',
 'total_count': 1,
 'result_set': [{'identifier': '6W9K',
   'score': 1.0,
   'services': [{'service_type': 'full_text',
     'nodes': [{'node_id': 8274,
       'original_score': 21.547258377075195,
       'norm_score': 1.0}]},
    {'service_type': 'text',
     'nodes': [{'node_id': 25834, 'original_score': 1.0, 'norm_score': 1.0},
      {'node_id': 13342, 'original_score': 1.0, 'norm_score': 1.0},
      {'node_id': 13170, 'original_score': 1.0, 'norm_score': 1.0}]}]}]}

Формирую запрос на получение нужной находки:

In [81]:
best_hit = search_result["result_set"][0] 
best_hit

{'identifier': '6W9K',
 'score': 1.0,
 'services': [{'service_type': 'full_text',
   'nodes': [{'node_id': 8274,
     'original_score': 21.547258377075195,
     'norm_score': 1.0}]},
  {'service_type': 'text',
   'nodes': [{'node_id': 25834, 'original_score': 1.0, 'norm_score': 1.0},
    {'node_id': 13342, 'original_score': 1.0, 'norm_score': 1.0},
    {'node_id': 13170, 'original_score': 1.0, 'norm_score': 1.0}]}]}

Получаю идентификатор лучшей находки. Дальше работаю с ней.

<h1> Задание №2 </h1>
Введя в поисковик на сайте RCSB PDB найденный мною идентификатор, мне удалось найти статью. Суть ее заключается в том, что ученые модифицировали традиционные препараты, которые используются для лечения мышечной дистрофии Дюшенна. Модификация направлена на то, чтобы уменьшить побочные действия препарата. 
Для клинического лечения болезни используются кортикостероиды, такие как преднизолон (ключевое слово) и дефлазакорт, которые сильно подавляют передачу сигналов NF-κB и воздействуют на глюкокортикоидный рецептор (GR). При длительном лечении кортикостероидами, пациенты с МДД испытывают неблагоприятные побочные эффекты. При тестировании иного препарата (ваморолона) было замечено, что он уменьшает воспаление мышц и уменьшает побочные эффекты, наблюдаемые при лечении другими кортикостероидами. Исследования показали, что ключевая водородная связь GR-лиганд невозможна в ваморолоне. 

<h1>Задание №3</h1>

Импортирую необходимое:

In [82]:
from ipywidgets import interact, fixed

Просматривую структуру:

In [83]:
view = nv.show_pdbid('6W9K') 
view

NGLWidget()

Создаю список необходимых для данной структуры отображений:

In [84]:
my_examples = {
    'Example 1': {
        'description': '''
Белок в виде cartoon, покраска по типу вторичной структуры, показана поверхность, с непрозрачностью 0.1,
лиганды в виде hyperball, покрашены в оттенок желтого.
''',
        'representations': [
            {
                'type': 'cartoon',                      
                'params': {
                    'sele': 'protein',               
                    'color': 'sstruc'  
                 }
            },
            { 
                'type': 'surface',                      
                'params': {
                    'sele': 'protein',                
                    'color': 'white',
                    'opacity': 0.1
                 }
                
            },
            {
                'type': 'hyperball',                      
                'params': {
                    'sele': 'ligand',                
                    'color': 'gold'  
                 }
            },
        ],
    },
    'Example 2': {
        'description': '''
Белок в виде cartoon темно-серого цвета,
боковые радикалы в виде линий светло-серого цвета,
боковые радикалы полярных аминокислот в виде hyperball, покрашены по элементам,
лиганды в шаростержневой модели, покрашены по элементам, углероды покрашены в темно-синий.
''',
        'representations': [
            {
                'type': 'cartoon',                      
                'params': {
                    'sele': 'protein',               
                    'color': 'DimGrey'  
                 }
            },
            {
                'type': 'backbone',                      
                'params': {
                    'sele': 'sidechainAttached',                     
                    'color': '#4d4d4d'  
                 }
            },
            {
                'type': 'hyperball',                      
                'params': {
                    'sele': 'sidechainAttached' and 'polar',                     
                    'color': 'element'  
                 }
            },
             {
                'type': 'ball+stick',                      
                'params': {
                    'sele': 'ligand and not _C',                     
                    'color': 'element'  
                 }
            },
            {
                'type': 'ball+stick',                      
                'params': {
                    'sele': 'ligant and _C',                     
                    'color': '#050515'  
                 }
            },
                 
        ],
    },
    'Example 3': {
        'description': '''
Белок в виде ribbon, покрашенной градиентом от N к C концу,
боковые радикалы в стержневой модели, покрашенные по элементам,
углероды гидрофобных аминокислот покрашены в светло-желтый,
углероды полярных заряженных аминокислот покрашены в светло-голубой,
лиганды не показаны никак.
''',
        'representations': [
            {
                'type': 'ribbon',                      
                'params': {
                    'sele': 'protein',               
                    'color': 'residueindex'  
                 }
            },
            {
                'type': 'licorice',                      
                'params': {
                    'sele': 'sidechainAttached',                     
                    'color': 'element'  
                 }
            },
            {
                'type': 'licorice',                      
                'params': {
                    'sele': 'sidechainAttached and hydrophobic and _C',                     
                    'color': '#FFFACD'  
                 }
            },
            {
                'type': 'liocorice',
                'params': {
                    'sele': 'sidechainAttached and polar and charged and _C',                     
                    'color': 'LightBlue'  
                 }
            },
        ],
    },
}

Формирую интерактивную ячейку:

In [85]:
def show_examples(view, example_name):
    view.clear()
    example = my_examples[example_name]
    print(example['description'])
    view.set_representations(example['representations'])
    view.center()

view = nv.show_pdbid("6W9K", default_representation=False)
interact(show_examples, view=fixed(view), example_name=list(my_examples.keys()))
view

interactive(children=(Dropdown(description='example_name', options=('Example 1', 'Example 2', 'Example 3'), va…

NGLWidget()